### Vestland database for ML

Linn Alexandra Emhjellen. 2021

In [1]:
import numpy as np
import pandas as pd
import os
import joblib
import matplotlib.pyplot as plt
from sklearn.preprocessing import OneHotEncoder

from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split

In [2]:
# random pixels from Vestland with GIS-features. For validation at the end
#df_random_Vestland = pd.read_excel('Vestland_pixels_2.xlsx')
#df_random_Vestland = pd.read_excel('Lærdal_Aurland_500k_pixels2.xlsx')
#df_Vestland_database = pd.read_excel('test_area_pixel_features.xlsx')
#df_Vestland_database = pd.read_excel('Lærdal_gård_bø_fishnet20_label_features.xlsx')
#df_Vestland_database = pd.read_excel('copy of Lærdal_Aurland_close_area_10_m_pixels_features.xlsx')

#df_Vestland_database = pd.read_csv('lærdal_aurland_10m_pixels_close.csv')

#df_Vestland_database = pd.read_csv('Vestland_West_features_10m.csv')
df_Vestland_database = pd.read_csv('Bohme_features_20m.csv')
df_Vestland_database = df_Vestland_database.dropna()

In [3]:
#encode bedrock values

bedrock = df_Vestland_database[["Bedrock"]]

bedrock_encoder = OneHotEncoder()
bedrock_encoded = bedrock_encoder.fit_transform(bedrock)

bedrock = bedrock_encoded.toarray()
bedrock_encoder.categories_

[array([108, 113, 143, 402, 423, 426, 432, 437, 440], dtype=int64)]

In [6]:
# sorted same as array 

#bedrock_groups = ['Granit','Granodiorite','Monzonite','Monzodiorite', 'Gabbro','Pyroksenite','Charnockite','Anorthosite','Rhyolite','Phyllite','Calcareous phyllite','Metasandstone', 'Quartzite','Quartz schist','Mica gneiss','Amphibole gneiss','Granitic gneiss','Tonalitic gneiss','Monzonitic gneiss','Orthopyroxene gneiss','Banded gneiss','Amphibolite','Metagabbro']

#bedrock_Vestland = ['Granite','Granodiorite','Tonalite','Trondhjemite','Syenite','Monzonite','Monzodiorite','Quartz diorite','Diorite','Gabbro','Norite','Peridotite','Pyroksenite','Charnockite','Mangerite','Anorthosite','Mafic dyke (Diabase, Dolerite)','Pegmatite/aplite','Felsic volcanic rock','Rhyolite','Dacite','Intermediate volcanic rock','Andesite','Mafic volcanic rock','Basalt',
                 # 'Pyroclastic rock','Volcanic breccia','Siltstone','Sandstone','Greywacke','Arkose','Konglomerate','Sedimentary breccia','Limestone','Tuffite','Shale','Phyllite','Mica schist','Garnet mica schist','Calcareous phyllite','Calcareous mica schist','Amphibole schist','Graphitic schist','Calcite marble',
                 #'Metasandstone','Metagreywacke','Meta-arkose','Quartzite','Quartz schist','Mica gneiss','Calc-silicate rock','Amphibole gneiss','Granitic gneiss','Granodioritic gneiss','Tonalitic gneiss','Quartz dioritic gneiss','Monzonitic gneiss','Dioritic gneis','Orthopyroxene gneiss','Migmatite','Augengneiss',
                 #'Banded gneiss','Greenschist','Greenstone','Amphibolite','Metagabbro','Eclogite','Serpentinite','Mylonite/Phyllonite','Cataclasite']

#bedrock_Vestland = ['Granite','Granodiorite','Monzonite','Monzodiorite','Quartx diorite','Gabbro','Pyroksenitt','Charnockitt','Anorthosite','Rhyolite','Phyllite','Calcareous phyllite','Metasandstone','Quartzite','Quartz schist','Mica gneiss','Amphibole gneiss','Granitic gneiss','Granodioritic gneiss','Tonalitic gneiss','Monzonitic gneiss','Orthopyroxene gneiss','Migmatite','Augengneiss','Banded gneiss','Amphibolite','Metagabbro','Mylonite/Phyllonite','Cataclasite']
#bedrock_Vestland = ['Granite','Monzonite','Monzodiorite','Charnockite','Granitic gneiss','Tonalitic gneiss']
#bedrock_Vestland = ['Granite','Granodiorite','Monzonite','Monzodiorite','Gabbro','Charnockite','Anorthosite','Phyllite','Quartzite','Granitic gneiss','Tonalitic gneiss','Orthopyroxene gneiss','Cataclasite']

#bedrock_Vestland = ['Granit','Monzonite','Monzodiorite','Charnockite','Anorthosite','Granitic gneiss','Tonalitic gneiss']
#bedrock_Vestland = ['Tonalite','Diorite','Gabbro','Anorthosite','Rhyolite','Dacite','Sandstone','Arkose','Konglomerate','Phyllite',
                  # 'Mica schist','Quartzite','Quartz schist','Granitic gneiss','Granodioritic gneiss','Tonalitic gneiss','Migmatite','Banded gneiss','Greenschist',
                   #'Greenstone','Amphibolite','Metagabbro','Serpentinite']
        
#bedrock_Vestland = ['Dacite','Sandstone','Konglomerate','Mica schist','Quartz schist','Granitic gneiss','Tonalitic gneiss','Banded gneiss','Amphibolite']
bedrock_Vestland = ['Monzonite','Gabbro','Anorthosite','Phyllite','Tonalitic gneiss','Mica gneiss','Tonalitic gneiss','Orthopyroxene gneiss','Migmatite']
df_bedrock = pd.DataFrame(bedrock, columns=bedrock_Vestland)

In [7]:
# merging the one-hot-encoded bedrock dataframe to the other parameters
df_Vestland_database = df_Vestland_database.reset_index()   #Need to do this, don't know why indexes was changed.
df_Vestland_database = pd.concat([df_Vestland_database, df_bedrock], axis=1)

In [8]:
aspect_categorical = []

for i in df_Vestland_database['Aspect']:
    if (i== -1):
        aspect_categorical.append('Flat')
    elif (i<= 22.5) & (i >= 0) or (i>= 337.5) & (i < 360):
        aspect_categorical.append('North')
    elif (i<= 67.5) & (i > 22.5):
        aspect_categorical.append('North East')
    elif (i<= 112.5) & (i > 67.5):
        aspect_categorical.append('East')
    elif (i <= 157.5) & (i > 112.5):
        aspect_categorical.append('South East')
    elif (i <= 202.5) & (i > 157.5):
        aspect_categorical.append('South')
    elif (i<= 247.5) & (i > 202.5):
        aspect_categorical.append('South West')
    elif (i<= 292.5) & (i > 247.5):
        aspect_categorical.append('West')
    elif (i<= 337.5) & (i > 292.5):
        aspect_categorical.append('North West')
    else:
        aspect_categorical.append('NaN')

In [9]:
df_Vestland_database['aspect_categorical'] = aspect_categorical

In [11]:
df_Vestland_database = df_Vestland_database.dropna()

In [12]:
# encode aspect values

from sklearn.preprocessing import OneHotEncoder
aspect_cat = df_Vestland_database[["aspect_categorical"]]

aspect_encoder = OneHotEncoder()
aspect_encoded = aspect_encoder.fit_transform(aspect_cat)

aspect= aspect_encoded.toarray()
aspect_encoder.categories_

[array(['East', 'Flat', 'North', 'North East', 'North West', 'South',
        'South East', 'South West', 'West'], dtype=object)]

In [13]:
# sorted same as array 
aspect_groups = ('East','Flat','North','North East','North West','South','South East','South West','West')

df_aspect = pd.DataFrame(aspect, columns=aspect_groups)

In [14]:
# adding Flat as a column as well
#array = np.zeros([len(df_Vestland_database),1])
#df_flat = pd.DataFrame(array, columns = ['Flat'])



In [15]:
df_Vestland_database

index     OID_     POINT_X       POINT_Y   Elevation      Slope  \
0              0        1  61314.5741  6.804053e+06  785.760925  42.661743   
1              1        2  61324.5741  6.804053e+06  775.545593  44.813194   
2              2        3  61334.5741  6.804053e+06  766.137207  39.271423   
3              3        4  61344.5741  6.804053e+06  759.246948  32.916458   
4              4        5  61354.5741  6.804053e+06  753.402039  29.343985   
...          ...      ...         ...           ...         ...        ...   
2047930  2562256  2562257  69554.5741  6.816453e+06  661.918884   8.343645   
2047931  2562257  2562258  69564.5741  6.816453e+06  661.912476   9.202660   
2047932  2562258  2562259  69574.5741  6.816453e+06  661.536682   9.152455   
2047933  2562259  2562260  69584.5741  6.816453e+06  659.753784  10.504866   
2047934  2562260  2562261  69594.5741  6.816453e+06  657.857422  11.790175   

             Aspect  Curvature  Profile_curv  Plan_curv  ...  Bedrock  \
0         94.211853   3.051331     -2.636860   0.414471  ...      113   
1         94.644402   0.926636      0.748065   1.674701  ...      113   
2         96.103744  -1.371216      2.497010   1.125794  ...      113   
3         99.230545   0.535461      0.843176   1.378637  ...      113   
4        103.750122   0.747192      0.374238   1.121430  ...      113   
...             ...        ...           ...        ...  ...      ...   
2047930   15.816636  -2.953735      1.943575  -1.010160  ...      108   
2047931   21.742188   0.115234      0.320242   0.435476  ...      108   
2047932   44.141239   2.452026     -0.862458   1.589569  ...      108   
2047933   62.287079   0.200867      0.062948   0.263814  ...      108   
2047934   68.847740  -0.410706     -0.070160  -0.480866  ...      108   

         Monzonite  Diorite  Anorthosite  Garnet mica schist  Mica gneiss  \
0              0.0      1.0          0.0                 0.0          0.0   
1              0.0      1.0          0.0                 0.0          0.0   
2              0.0      1.0          0.0                 0.0          0.0   
3              0.0      1.0          0.0                 0.0          0.0   
4              0.0      1.0          0.0                 0.0          0.0   
...            ...      ...          ...                 ...          ...   
2047930        1.0      0.0          0.0                 0.0          0.0   
2047931        1.0      0.0          0.0                 0.0          0.0   
2047932        1.0      0.0          0.0                 0.0          0.0   
2047933        1.0      0.0          0.0                 0.0          0.0   
2047934        1.0      0.0          0.0                 0.0          0.0   

         Tonalitic gneiss  Orthopyroxene gneiss  Migmatite  aspect_categorical  
0                     0.0                   0.0        0.0                East  
1                     0.0                   0.0        0.0                East  
2                     0.0                   0.0        0.0                East  
3                     0.0                   0.0        0.0                East  
4                     0.0                   0.0        0.0                East  
...                   ...                   ...        ...                 ...  
2047930               0.0                   0.0        0.0               North  
2047931               0.0                   0.0        0.0               North  
2047932               0.0                   0.0        0.0          North East  
2047933               0.0                   0.0        0.0          North East  
2047934               0.0                   0.0        0.0                East  

[2047935 rows x 24 columns]

In [14]:
# merging the one-hot-encoded bedrock dataframe to the other parameters
#df_Vestland_database = df_Vestland_database.reset_index()   #Need to do this, don't know why indexes was changed.
df_Vestland_database = pd.concat([df_Vestland_database, df_aspect], axis=1)


#df_Vestland_database = pd.concat([df_Vestland_database, df_flat], axis=1)

In [15]:
df_Vestland_database.columns

Index(['index', 'OID_', 'POINT_X', 'POINT_Y', 'Elevation', 'Slope', 'Aspect',
       'Profile_curv', 'Plan_curv', 'Flow_dir', 'Flow_acc',
       'Distance_to_roads', 'TRI', 'Bedrock', 'Monzonite', 'Gabbro',
       'Anorthosite', 'Phyllite', 'Tonalitic gneiss', 'Mica gneiss',
       'Tonalitic gneiss', 'Orthopyroxene gneiss', 'Migmatite',
       'aspect_categorical', 'East', 'Flat', 'North', 'North East',
       'North West', 'South', 'South East', 'South West', 'West'],
      dtype='object')

In [ ]:
#df_Vestland_database['Flow_dir'] = 0

In [16]:
# selcted features

#Vestland_features = df_Vestland_database[['POINT_X', 'POINT_Y',
#     'Elevation', 'Slope', 'Aspect', 'Profile_curv',
#       'Plan_curv', 'Flow_dir', 'Flow_acc', 'Distance_to_roads', 'TRI',
#      'Bedrock', 'Granite', 'Granodiorite', 'Tonalite', 'Trondhjemite',
#       'Syenite', 'Monzonite', 'Monzodiorite', 'Quartz diorite', 'Diorite',
#      'Gabbro', 'Norite', 'Peridotite', 'Pyroksenite', 'Charnockite',
#       'Mangerite', 'Anorthosite', 'Mafic dyke (Diabase, Dolerite)',
#       'Pegmatite/aplite', 'Felsic volcanic rock', 'Rhyolite', 'Dacite',
#       'Intermediate volcanic rock', 'Andesite', 'Mafic volcanic rock',
#       'Basalt', 'Pyroclastic rock', 'Volcanic breccia', 'Siltstone',
#       'Sandstone', 'Greywacke', 'Arkose', 'Konglomerate',
#       'Sedimentary breccia', 'Limestone', 'Tuffite', 'Shale', 'Phyllite',
#       'Mica schist', 'Garnet mica schist', 'Calcareous phyllite',
#       'Calcareous mica schist', 'Amphibole schist', 'Graphitic schist',
#       'Calcite marble', 'Metasandstone', 'Metagreywacke', 'Meta-arkose',
#       'Quartzite', 'Quartz schist', 'Mica gneiss', 'Calc-silicate rock',
#       'Amphibole gneiss', 'Granitic gneiss', 'Granodioritic gneiss',
#       'Tonalitic gneiss', 'Quartz dioritic gneiss', 'Monzonitic gneiss',
#       'Dioritic gneis', 'Orthopyroxene gneiss', 'Migmatite', 'Augengneiss',
#       'Banded gneiss', 'Greenschist', 'Greenstone', 'Amphibolite',
#       'Metagabbro', 'Eclogite', 'Serpentinite', 'Mylonite/Phyllonite',
#       'Cataclasite', 'aspect_categorical', 'East', 'North', 'North East',
#       'North West', 'South', 'South East', 'South West', 'West', 'Flat']].copy()
        
        
#Vestland_features = df_Vestland_database[['POINT_X','POINT_Y','Elevation', 'Slope', 'East', 'North', 'North East','North West', 'South', 'South East', 'South West', 'West', 'Flat', 'Profile_curv',
      # ""'Plan_curv', 'Flow_dir', 'Flow_acc', 'Distance_to_roads', 'TRI', 'Granite','Granodiorite','Monzonite','Monzodiorite','Quartx diorite','Gabbro','Pyroksenitt','Charnockitt','Anorthosite','Rhyolite','Phyllite','Calcareous phyllite','Metasandstone','Quartzite','Quartz schist','Mica gneiss','Amphibole gneiss','Granitic gneiss','Granodioritic gneiss','Tonalitic gneiss','Monzonitic gneiss','Orthopyroxene gneiss','Migmatite','Augengneiss','Banded gneiss','Amphibolite','Metagabbro','Mylonite/Phyllonite','Cataclasite']].copy()


#target = df_Vestland_database[['POINT_X', 'POINT_Y']].copy()

#Vestland_features = df_Vestland_database[['POINT_X', 'POINT_Y', 'Elevation',
    #   'Slope', 'Aspect', 'Profile_curv', 'Plan_curv', 'Flow_dir', 'Flow_acc',
     #  'Distance_to_roads', 'TRI', 'Bedrock', 'Granite', 'Monzonite',
      # 'Monzodiorite', 'Charnockite', 'Granitic gneiss', 'Tonalitic gneiss',
       #'aspect_categorical', 'East', 'North', 'North East', 'North West',
       #'#South', 'South East', 'South West', 'West', 'Flat']].copy()
    
    
#Vestland_features = df_Vestland_database[['POINT_X', 'POINT_Y', 'Elevation',
 #    'Slope', 'Aspect', 'Profile_curv', 'Plan_curv', 'Flow_dir', 'Flow_acc',
 #    'Distance_to_roads', 'TRI', 'Bedrock', 'Monzonite','Monzodiorite','Charnockite','Anorthosite','Granitic gneiss','Tonalitic gneiss',
 #   'aspect_categorical', 'East', 'North', 'North East', 'North West',
 #   'South', 'South East', 'South West', 'West', 'Flat']].copy()

Vestland_features = df_Vestland_database[['POINT_X', 'POINT_Y', 'Elevation',
     'Slope', 'Aspect', 'Profile_curv', 'Plan_curv', 'Flow_dir', 'Flow_acc',
     'Distance_to_roads', 'TRI', 'Bedrock', 'Monzonite','Gabbro','Anorthosite','Phyllite','Tonalitic gneiss','Mica gneiss','Tonalitic gneiss','Orthopyroxene gneiss','Migmatite',
    'aspect_categorical', 'East', 'North', 'North East', 'North West',
    'South', 'South East', 'South West', 'West', 'Flat']].copy()


In [17]:
#Vestland_features.to_csv("ML_Vestland_West_10_m_database.csv")
Vestland_features.to_csv('ML_bohme_20m.csv')